# Let's solve q classification  problem on  kaggle

**Problem:** [BrisT1D Blood Glucose Prediction Competition](https://www.kaggle.com/competitions/brist1d/overview).

## reading data from kaggle

In [5]:
!pip install -q kaggle


[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [6]:
# from google.colab import files
# _ = files.upload()

In [7]:
# !mkdir -p ~/.kaggle
# !mv kaggle.json ~/.kaggle/
# !chmod 600 ~/.kaggle/kaggle.json

In [8]:
! kaggle competitions download -c brist1d


  0%|          | 0.00/9.21M [00:00<?, ?B/s]
 11%|█         | 1.00M/9.21M [00:00<00:06, 1.26MB/s]
 22%|██▏       | 2.00M/9.21M [00:01<00:03, 2.15MB/s]
 33%|███▎      | 3.00M/9.21M [00:01<00:02, 2.19MB/s]
 43%|████▎     | 4.00M/9.21M [00:01<00:02, 2.27MB/s]
 54%|█████▍    | 5.00M/9.21M [00:02<00:01, 2.58MB/s]
 65%|██████▌   | 6.00M/9.21M [00:02<00:01, 2.51MB/s]
 76%|███████▌  | 7.00M/9.21M [00:03<00:00, 2.58MB/s]
 87%|████████▋ | 8.00M/9.21M [00:03<00:00, 2.58MB/s]
 98%|█████████▊| 9.00M/9.21M [00:04<00:00, 2.42MB/s]
100%|██████████| 9.21M/9.21M [00:04<00:00, 2.40MB/s]


In [10]:
!dir

 Le volume dans le lecteur C n'a pas de nom.
 Le num�ro de s�rie du volume est C812-4650

 R�pertoire de c:\Users\pc\Desktop\british-airways

21/11/2024  11:13    <DIR>          .
20/11/2024  14:52    <DIR>          ..
09/09/2024  20:40         9�652�764 brist1d.zip
21/11/2024  11:14         1�285�529 BrisT1D_Blood_Glucose_Prediction_Competition.ipynb
21/11/2024  03:06               289 Cybertronics.csv
21/11/2024  02:55            23�812 Cybertronics.xlsx
20/11/2024  17:40    <DIR>          data
21/11/2024  02:23            33�541 Jefferson Property.xlsx
21/11/2024  02:30             9�870 Jefferson-Property.csv
21/11/2024  03:06            14�740 p.ipynb
               7 fichier(s)       11�020�545 octets
               3 R�p(s)  206�113�959�936 octets libres


In [11]:
!unzip brist1d.zip

Archive:  brist1d.zip
  inflating: activities.txt          
  inflating: sample_submission.csv   
  inflating: test.csv                
  inflating: train.csv               


## Load data

In [12]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from matplotlib_inline.backend_inline import set_matplotlib_formats
set_matplotlib_formats('svg')

In [13]:
def load_datasets():
  try:
    train = pd.read_csv("train.csv")
    test = pd.read_csv("test.csv")
    sample_submission = pd.read_csv("sample_submission.csv")
    print("Data sets loaded successufly")
    return train ,test ,sample_submission
  except Exception  as e:
    print(f"Exception loading data {e}")
    return None


In [14]:
train,test,sample_submission = load_datasets()

C:\Users\pc\AppData\Local\Temp\ipykernel_7192\1896559776.py:3: DtypeWarning: Columns (435,436,437,438,439,440,441,442,443,444,445,446,447,448,449,450,451,452,453,454,455,456,457,458,459,460,461,462,463,464,465,466,467,468,469,470,471,472,473,474,475,476,477,478,479,480,481,482,483,484,485,486,487,488,489,490,491,492,493,494,495,496,497,498,499,500,501,502,503,504,505,506) have mixed types. Specify dtype option on import or set low_memory=False.
  train = pd.read_csv("train.csv")


Data sets loaded successufly


## Dataset information

In [15]:
def display_dataset_info(dataset,name):
  print("------------------------------------------------------------")
  print(f"{name} DataFrame shape : Rows = {dataset.shape[0]}, Columns = {dataset.shape[1]}")
  total_missing = dataset.isnull().sum().sum()
  print(f"there are total {total_missing} missing values in {name} DataFrame") if total_missing > 0 else print(f"There are no missing values in {name} DataFrame")
  total_duplicated = dataset.duplicated().sum()
  print(f"there are total {total_duplicated} duplicated values in {name} DataFrame") if total_duplicated > 0 else print(f"There are no duplicated values in {name} DataFrame")
  display(dataset.describe().style.set_caption(f"Descriptive Statistics for {name} Dataset").background_gradient(cmap="coolwarm"))



  print("**************************************************************")
datasets = [train, test, sample_submission]
names = [ "Train", "Test", "Sample"]
for i in range(len(datasets)):
    display_dataset_info(datasets[i], names[i])


------------------------------------------------------------
Train DataFrame shape : Rows = 177024, Columns = 508
there are total 40294794 missing values in Train DataFrame
There are no duplicated values in Train DataFrame


**************************************************************
------------------------------------------------------------
Test DataFrame shape : Rows = 3644, Columns = 507
there are total 862409 missing values in Test DataFrame
There are no duplicated values in Test DataFrame


**************************************************************
------------------------------------------------------------
Sample DataFrame shape : Rows = 3644, Columns = 2
There are no missing values in Sample DataFrame
There are no duplicated values in Sample DataFrame


**************************************************************


## Feature selection




In [16]:
from sklearn.preprocessing import LabelEncoder

categorical_columns = train.select_dtypes(include="object").columns
for column in categorical_columns:
  le = LabelEncoder()
  train[column] = le.fit_transform(train[column])
  test[column] = le.fit_transform(test[column])



In [17]:
numeric_columns = train.select_dtypes("number")
train = train.dropna(thresh=int(0.6*len(train)),axis=1)

In [18]:
variances = numeric_columns.var()
variances

id               2.611473e+09
p_num            6.897616e+00
time             6.841471e+03
bg-5:55          8.134974e+00
bg-5:50          8.488124e+00
                     ...     
activity-0:15    1.061428e+00
activity-0:10    1.066891e+00
activity-0:05    1.067976e+00
activity-0:00    1.071752e+00
bg+1:00          8.978403e+00
Length: 508, dtype: float64

In [19]:
low_variance_columns = variances[variances < 1].index.to_list()

In [20]:
train = train.drop(columns=low_variance_columns)

In [21]:
print("Droped columns with low variance : ",low_variance_columns)

Droped columns with low variance :  ['activity-4:10', 'activity-4:00', 'activity-3:55', 'activity-3:45', 'activity-3:40', 'activity-3:30', 'activity-3:25', 'activity-3:15', 'activity-3:10', 'activity-3:00', 'activity-2:55', 'activity-2:45', 'activity-2:40', 'activity-2:30', 'activity-2:25', 'activity-2:20', 'activity-2:15', 'activity-2:10', 'activity-2:00', 'activity-1:55', 'activity-1:50', 'activity-1:45', 'activity-1:40', 'activity-1:35', 'activity-1:30', 'activity-1:25', 'activity-1:20', 'activity-1:15', 'activity-1:10', 'activity-1:05', 'activity-1:00', 'activity-0:55', 'activity-0:50', 'activity-0:45', 'activity-0:40', 'activity-0:35', 'activity-0:30', 'activity-0:25']


In [22]:
display_dataset_info(train,"train")

------------------------------------------------------------
train DataFrame shape : Rows = 177024, Columns = 326
there are total 8317541 missing values in train DataFrame
There are no duplicated values in train DataFrame


**************************************************************


In [23]:
print("Total number of columns with low variance : ",len(low_variance_columns))

Total number of columns with low variance :  38


**Summary of results**

---

The initial dataset had a total of **40294794** missing values after removing the columns with more than 60% missing values, the remaining missing values were reduced to **8317541**.
Also 38 columns with low variacne were droped

In [24]:
import seaborn as sns

correlation_matrix = train.corr()
#plt.figure(figsize=(12, 10))
#sns.heatmap(correlation_matrix, annot=True, cmap="coolwarm", fmt=".2f", linewidths=0.5)
#plt.title("Correlation Matrix", fontsize=16)
#plt.show()

In [25]:
correlation_matrix

id     p_num      time   bg-5:55   bg-5:50   bg-5:45  \
id             1.000000  0.985712  0.003415 -0.115540 -0.114765 -0.113206   
p_num          0.985712  1.000000  0.004015 -0.120308 -0.118613 -0.116076   
time           0.003415  0.004015  1.000000 -0.075836 -0.070592 -0.073961   
bg-5:55       -0.115540 -0.120308 -0.075836  1.000000  0.992528  0.975774   
bg-5:50       -0.114765 -0.118613 -0.070592  0.992528  1.000000  0.992529   
...                 ...       ...       ...       ...       ...       ...   
activity-0:15 -0.000591 -0.009142 -0.059943  0.029934  0.025614  0.021669   
activity-0:10 -0.000049 -0.008580 -0.059233  0.030209  0.025872  0.023152   
activity-0:05  0.000122 -0.008392 -0.058724  0.030396  0.025850  0.022793   
activity-0:00 -0.000376 -0.009014 -0.058397  0.030650  0.026164  0.021796   
bg+1:00       -0.112105 -0.114722  0.075510  0.144346  0.131167  0.136448   

                bg-5:40   bg-5:35   bg-5:30   bg-5:25  ...  activity-3:05  \
id            -0.115608 -0.114831 -0.113203 -0.115672  ...      -0.001279   
p_num         -0.120316 -0.118667 -0.115996 -0.120315  ...      -0.010224   
time          -0.076960 -0.072037 -0.075775 -0.078588  ...      -0.068294   
bg-5:55        0.953065  0.926544  0.897773  0.867544  ...       0.023509   
bg-5:50        0.975781  0.954475  0.926662  0.897823  ...       0.018116   
...                 ...       ...       ...       ...  ...            ...   
activity-0:15  0.028986  0.024924  0.020230  0.027908  ...       0.052260   
activity-0:10  0.029420  0.025440  0.021900  0.028087  ...       0.050994   
activity-0:05  0.029546  0.024922  0.021708  0.028308  ...       0.052678   
activity-0:00  0.029634  0.025256  0.020622  0.028614  ...       0.050844   
bg+1:00        0.143770  0.130724  0.136183  0.142579  ...       0.002148   

               activity-2:50  activity-2:35  activity-2:05  activity-0:20  \
id                 -0.001768      -0.001804      -0.001436       0.000285   
p_num              -0.010609      -0.010558      -0.010114      -0.008149   
time               -0.068608      -0.070105      -0.070707      -0.060333   
bg-5:55             0.024804       0.027045       0.033455       0.029738   
bg-5:50             0.019487       0.020631       0.025628       0.024367   
...                      ...            ...            ...            ...   
activity-0:15       0.057844       0.061745       0.078049       0.859438   
activity-0:10       0.056038       0.061320       0.074892       0.726132   
activity-0:05       0.055629       0.062627       0.072210       0.601284   
activity-0:00       0.052416       0.058613       0.068813       0.485985   
bg+1:00             0.001640       0.002123       0.004774       0.016504   

               activity-0:15  activity-0:10  activity-0:05  activity-0:00  \
id                 -0.000591      -0.000049       0.000122      -0.000376   
p_num              -0.009142      -0.008580      -0.008392      -0.009014   
time               -0.059943      -0.059233      -0.058724      -0.058397   
bg-5:55             0.029934       0.030209       0.030396       0.030650   
bg-5:50             0.025614       0.025872       0.025850       0.026164   
...                      ...            ...            ...            ...   
activity-0:15       1.000000       0.862656       0.731395       0.598060   
activity-0:10       0.862656       1.000000       0.865363       0.727456   
activity-0:05       0.731395       0.865363       1.000000       0.859179   
activity-0:00       0.598060       0.727456       0.859179       1.000000   
bg+1:00             0.019279       0.023082       0.025048       0.028256   

                bg+1:00  
id            -0.112105  
p_num         -0.114722  
time           0.075510  
bg-5:55        0.144346  
bg-5:50        0.131167  
...                 ...  
activity-0:15  0.019279  
activity-0:10  0.023082  
activity-0:05  0.025048  
activity-0:00  0.028256  
bg+1:00        1.000000  

[326 row

In [26]:
target_column = 'bg+1:00'
correlations = correlation_matrix[target_column]

print("Correlations with bg+1:00:")
#print(correlations.sort_values(ascending=False))


strongly_correlated_columns = correlations[correlations.abs() > 0.5].index.to_list()

no_missing_columns = train.columns[train.isnull().sum() == 0].to_list()


Correlations with bg+1:00:


In [27]:
strongly_correlated_columns

['bg-0:35',
 'bg-0:30',
 'bg-0:25',
 'bg-0:20',
 'bg-0:15',
 'bg-0:10',
 'bg-0:05',
 'bg-0:00',
 'bg+1:00']

In [28]:
no_missing_columns

['id',
 'p_num',
 'time',
 'activity-5:55',
 'activity-5:50',
 'activity-5:45',
 'activity-5:40',
 'activity-5:35',
 'activity-5:30',
 'activity-5:25',
 'activity-5:20',
 'activity-5:15',
 'activity-5:10',
 'activity-5:05',
 'activity-5:00',
 'activity-4:55',
 'activity-4:50',
 'activity-4:45',
 'activity-4:40',
 'activity-4:35',
 'activity-4:30',
 'activity-4:25',
 'activity-4:20',
 'activity-4:15',
 'activity-4:05',
 'activity-3:50',
 'activity-3:35',
 'activity-3:20',
 'activity-3:05',
 'activity-2:50',
 'activity-2:35',
 'activity-2:05',
 'activity-0:20',
 'activity-0:15',
 'activity-0:10',
 'activity-0:05',
 'activity-0:00',
 'bg+1:00']

In [29]:
final_selected_columns = strongly_correlated_columns + no_missing_columns



In [30]:
final_selected_columns

['bg-0:35',
 'bg-0:30',
 'bg-0:25',
 'bg-0:20',
 'bg-0:15',
 'bg-0:10',
 'bg-0:05',
 'bg-0:00',
 'bg+1:00',
 'id',
 'p_num',
 'time',
 'activity-5:55',
 'activity-5:50',
 'activity-5:45',
 'activity-5:40',
 'activity-5:35',
 'activity-5:30',
 'activity-5:25',
 'activity-5:20',
 'activity-5:15',
 'activity-5:10',
 'activity-5:05',
 'activity-5:00',
 'activity-4:55',
 'activity-4:50',
 'activity-4:45',
 'activity-4:40',
 'activity-4:35',
 'activity-4:30',
 'activity-4:25',
 'activity-4:20',
 'activity-4:15',
 'activity-4:05',
 'activity-3:50',
 'activity-3:35',
 'activity-3:20',
 'activity-3:05',
 'activity-2:50',
 'activity-2:35',
 'activity-2:05',
 'activity-0:20',
 'activity-0:15',
 'activity-0:10',
 'activity-0:05',
 'activity-0:00',
 'bg+1:00']

In [31]:
train = train[final_selected_columns]
test = test[[col for col in final_selected_columns if col in test.columns]]

**Summary of results**

---
We chose the columns bg-1:00 bg-0:45 bg-0:30 bg-0:15 and other blood glucose measurements because they show the strongest correlations with the target column bg+1:00. Additionally, we included other columns that have no null values

In [32]:
train.isnull().sum().sort_values(ascending=False)[:10].to_frame().style.background_gradient()

In [33]:
train.isnull().sum().sum()

134487

In [34]:
test.isnull().sum().sum()

5362

**Summary of results**
We still have 134,487 in train set and 5362 in test set missing values in our dataset, so we will use the KNN imputer to handle the remaining missing values



## Impute missing values

In [35]:
%%time
from sklearn.impute import KNNImputer

numeric_trainColl = train.select_dtypes("number")
numeric_testColl = test.select_dtypes("number")

imputer = KNNImputer(n_neighbors=5)
train_imputed = imputer.fit_transform(numeric_trainColl)
train = pd.DataFrame(train_imputed, columns=numeric_trainColl.columns)

#imputer = KNNImputer(n_neighbors=5)
#test_imputed = imputer.fit_transform(numeric_testColl)
# test = pd.DataFrame(test_imputed, columns=numeric_testColl.columns)

CPU times: total: 11min 28s
Wall time: 21min 43s


In [36]:
imputer = KNNImputer(n_neighbors=5)
test_imputed = imputer.fit_transform(numeric_testColl)
test = pd.DataFrame(test_imputed, columns=numeric_testColl.columns)

In [37]:
print("missing values in train set :",train.isnull().sum().sum())
print("missing values in test set :",train.isnull().sum().sum())

missing values in train set : 0
missing values in test set : 0


In [38]:
train = train.loc[:, ~train.columns.duplicated()]
test = test.loc[:, ~test.columns.duplicated()]

In [41]:
import plotly.express as px

fig = px.histogram(train,x=train[target_column],nbins=30,title="Histogramme of target")
fig.update_layout(xaxis_title="Value",yaxis_title="Frequency")
fig.show()

**summary of results** : 
The distrubution follow distrubution log-normale must value are 5 - 15


In [44]:
Q1= train[target_column].quantile(0.25)
Q3= train[target_column].quantile(0.75)

IQR = Q3 - Q1

lower_b = Q1 - 1.5 * IQR
upper_b = Q3 + 1.5* IQR

df_cleaned = train[(train[target_column]>=lower_b) & (train[target_column] <= upper_b)]


In [45]:
fig = px.histogram(df_cleaned,x=df_cleaned[target_column],nbins=30,title="Histogramme of target")
fig.update_layout(xaxis_title="Value",yaxis_title="Frequency")
fig.show()

In [46]:
df_cleaned.columns

Index(['bg-0:35', 'bg-0:30', 'bg-0:25', 'bg-0:20', 'bg-0:15', 'bg-0:10',
       'bg-0:05', 'bg-0:00', 'bg+1:00', 'id', 'p_num', 'time', 'activity-5:55',
       'activity-5:50', 'activity-5:45', 'activity-5:40', 'activity-5:35',
       'activity-5:30', 'activity-5:25', 'activity-5:20', 'activity-5:15',
       'activity-5:10', 'activity-5:05', 'activity-5:00', 'activity-4:55',
       'activity-4:50', 'activity-4:45', 'activity-4:40', 'activity-4:35',
       'activity-4:30', 'activity-4:25', 'activity-4:20', 'activity-4:15',
       'activity-4:05', 'activity-3:50', 'activity-3:35', 'activity-3:20',
       'activity-3:05', 'activity-2:50', 'activity-2:35', 'activity-2:05',
       'activity-0:20', 'activity-0:15', 'activity-0:10', 'activity-0:05',
       'activity-0:00'],
      dtype='object')

In [47]:
df_cleaned.head()

bg-0:35  bg-0:30  bg-0:25  bg-0:20  bg-0:15  bg-0:10  bg-0:05  bg-0:00  \
0     7.22     17.3    11.66     6.78     16.2    11.40     6.36     15.1   
1     7.22     16.2    11.66     6.78     15.1    11.40     6.36     14.4   
2     9.04     15.1    11.46     8.10     14.4    11.30     7.56     13.9   
3    14.72     14.4     6.48    14.72     13.9     8.46    14.72     13.8   
4     8.32     13.9     8.06     6.44     13.8     8.38     5.64     13.4   

   bg+1:00      id  ...  activity-3:20  activity-3:05  activity-2:50  \
0     13.4     0.0  ...           21.0           21.0           21.0   
1     12.8     1.0  ...           21.0           21.0           21.0   
2     15.5  1112.0  ...           21.0           21.0           21.0   
3     14.8  2223.0  ...           21.0           21.0           21.0   
4     12.7  3334.0  ...           21.0           21.0           21.0   

   activity-2:35  activity-2:05  activity-0:20  activity-0:15  activity-0:10  \
0           21.0           21.0           22.0           22.0           22.0   
1           21.0           21.0           22.0           22.0           22.0   
2           21.0           21.0           22.0           22.0           22.0   
3           21.0           21.0           22.0           22.0           22.0   
4           21.0           21.0           22.0           22.0           22.0   

   activity-0:05  activity-0:00  
0           22.0           22.0  
1           22.0           22.0  
2           22.0           22.0  
3           22.0           22.0  
4           22.0           22.0  

[5 rows x 46 columns]

In [57]:
from sklearn.metrics import mean_absolute_error
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.optimizers import Adam

X = df_cleaned.drop(columns=[target_column])
y = df_cleaned[target_column]


std = StandardScaler()
X_std = std.fit_transform(X)

X_train ,X_test , y_train ,y_test = train_test_split(X_std,y,test_size=0.2,random_state=42)


model = Sequential([
    Dense(64,input_dim=X_train.shape[1],activation='relu'),
    Dense(32,activation='relu'),
    Dense(1)
])


model.compile(optimizer=Adam(learning_rate=0.001), loss='mean_squared_error')

model.summary()

c:\Users\pc\AppData\Local\Programs\Python\Python312\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning:

Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.



Model: "sequential_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense_6 (Dense)                 │ (None, 64)             │         2,944 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_7 (Dense)                 │ (None, 32)             │         2,080 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_8 (Dense)                 │ (None, 1)              │            33 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 5,057 (19.75 KB)

 Trainable params: 5,057 (19.75 KB)

 Non-trainable params: 0 (0.00 B)

In [58]:
history = model.fit(X_train, y_train, epochs=100, batch_size=10, validation_split=0.2)

Epoch 1/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 24s 2ms/step - loss: 6.2903 - val_loss: 3.8759
Epoch 2/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 27s 2ms/step - loss: 3.7141 - val_loss: 3.6970
Epoch 3/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 26s 2ms/step - loss: 3.5722 - val_loss: 3.7438
Epoch 4/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 36s 3ms/step - loss: 3.5618 - val_loss: 3.6509
Epoch 5/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 21s 2ms/step - loss: 3.4963 - val_loss: 3.5747
Epoch 6/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 21s 2ms/step - loss: 3.4810 - val_loss: 3.5915
Epoch 7/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 23s 2ms/step - loss: 3.4598 - val_loss: 3.5858
Epoch 8/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 36s 3ms/step - loss: 3.4437 - val_loss: 3.5534
Epoch 9/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 37s 3ms/step - loss: 3.4263 - val_loss: 3.5543
Epoch 10/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 32s 3ms/step - loss: 3.3517 - val_loss: 3.4732
Epoch 11/100
11055/11055 ━━━━━━━━━━━━━━━━━━━━ 24s 2ms/step - loss: 3.3388 - val

In [61]:
from sklearn.metrics import mean_squared_error
predictions = model.predict(X_test)
rmse = np.sqrt(mean_squared_error(y_test,predictions))
print(rmse)

1080/1080 ━━━━━━━━━━━━━━━━━━━━ 1s 693us/step
1.8364562027519713


In [62]:
test_data = test.drop(columns=[col for col in ['bg+1:00'] if col in test.columns])
test_scaled = std.transform(test_data)
test_predictions = model.predict(test_scaled)

114/114 ━━━━━━━━━━━━━━━━━━━━ 0s 789us/step


In [63]:
test_predictions

array([[9.225355 ],
       [6.755515 ],
       [8.9777355],
       ...,
       [5.892145 ],
       [6.826296 ],
       [5.8752365]], dtype=float32)

In [64]:
df = pd.read_csv("sample_submission.csv")
df.head()

id  bg+1:00
0  p01_8459      9.6
1  p01_8460      4.6
2  p01_8461      8.0
3  p01_8462      9.9
4  p01_8463      5.3

In [80]:
submission = pd.DataFrame({
    'id':df['id'],
    'bg+1:00':test_predictions.flatten()
})

submission.head()

id   bg+1:00
0  p01_8459  9.225355
1  p01_8460  6.755515
2  p01_8461  8.977736
3  p01_8462  8.678785
4  p01_8463  5.275097

In [81]:
submission.to_csv("submission.csv",index=False)

In [ ]:
from xgboost import XGBRegressor

xgb_model = XGBRegressor(objective='reg:squarederror', n_estimators=100, random_state=42)

xgb_model.fit(X_train,y_train)



XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=0.1, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=None, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             multi_strategy=None, n_estimators=100, n_jobs=None,
             num_parallel_tree=None, random_state=42, ...)

In [129]:
predictions = xgb_model.predict(X_test)
rmse = mean_squared_error(y_test,predictions)
rmse

3.1943583637018462

In [122]:
predictions = xgb_model.predict(test_scaled)


In [123]:
submission = pd.DataFrame({
    'id':df['id'],
    'bg+1:00':predictions
})

submission.to_csv("submission_2.csv",index=False)